# 05.2 - SVM y Variantes Light

Aquí pruebo diferentes tipos de Support Vector Machines con configuraciones light pero variadas. La idea es explorar diferentes kernels, parámetros C y versiones de SVM para ver cuál funciona mejor con nuestros datos sin winsorizing.

Voy a usar principalmente LinearSVC para velocidad, pero también probaré SVC con kernels básicos.

In [1]:
# Importaciones para SVM
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from datetime import datetime
import time
import warnings
warnings.filterwarnings('ignore')

# Plotly
import plotly.graph_objects as go
import plotly.express as px
import plotly.figure_factory as ff
from plotly.subplots import make_subplots

# SVM variants
from sklearn.svm import SVC, LinearSVC, NuSVC
from sklearn.model_selection import train_test_split, StratifiedKFold, cross_val_score
from sklearn.metrics import (
    accuracy_score, precision_score, recall_score, f1_score,
    confusion_matrix, roc_curve, auc, precision_recall_curve,
    average_precision_score, roc_auc_score
)
from sklearn.preprocessing import StandardScaler
from sklearn.calibration import CalibratedClassifierCV  # Para obtener probabilidades en LinearSVC

import joblib
import json
import os

# Configuración
RANDOM_STATE = 42
np.random.seed(RANDOM_STATE)

print(f"Notebook 05.2 - SVM Variantes iniciado: {datetime.now().strftime('%Y-%m-%d %H:%M:%S')}")
print("Voy a probar múltiples configuraciones de SVM light")

Notebook 05.2 - SVM Variantes iniciado: 2025-08-20 17:59:10
Voy a probar múltiples configuraciones de SVM light


In [2]:
# Cargar datos (mismo setup que otros notebooks)
print("Cargando datos procesados sin winsorizing...")

df = pd.read_csv('../processed_data/dataset_features_processed.csv')
X = df.drop('BinaryNumTarget', axis=1)
y = df['BinaryNumTarget']

print(f"Datos: {X.shape[0]:,} muestras, {X.shape[1]} features")

# División consistente
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=RANDOM_STATE, stratify=y
)

# SVM necesita scaling obligatorio
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)

print(f"Train: {len(X_train):,}, Test: {len(X_test):,}")
print("StandardScaler aplicado (crítico para SVM)")
print(f"Rango escalado: [{X_train_scaled.min():.3f}, {X_train_scaled.max():.3f}]")

# Configuración CV
cv = StratifiedKFold(n_splits=5, shuffle=True, random_state=RANDOM_STATE)
resultados_svm = {}

Cargando datos procesados sin winsorizing...
Datos: 134,198 muestras, 57 features
Train: 107,358, Test: 26,840
StandardScaler aplicado (crítico para SVM)
Rango escalado: [-2.965, 309.499]


In [3]:
# Función para evaluar SVM con manejo especial de probabilidades
def evaluar_svm(modelo, nombre, X_train, X_test, y_train, y_test, cv, usar_calibracion=False):
    """
    Evalúo un modelo SVM específico.
    usar_calibracion: True para LinearSVC que no tiene predict_proba nativo.
    """
    print(f"\nEvaluando: {nombre}")
    print("-" * 50)
    
    start_time = time.time()
    
    # Si necesito calibración para probabilidades
    if usar_calibracion:
        print("Aplicando calibración para obtener probabilidades...")
        modelo_calibrado = CalibratedClassifierCV(modelo, method='sigmoid', cv=3)
        modelo_calibrado.fit(X_train, y_train)
        modelo_final = modelo_calibrado
    else:
        modelo.fit(X_train, y_train)
        modelo_final = modelo
    
    train_time = time.time() - start_time
    
    # Predicciones
    y_pred = modelo_final.predict(X_test)
    
    # Probabilidades
    y_pred_proba = None
    try:
        if hasattr(modelo_final, 'predict_proba'):
            y_pred_proba = modelo_final.predict_proba(X_test)[:, 1]
        elif hasattr(modelo_final, 'decision_function'):
            # Normalizo decision function a [0,1]
            decision_scores = modelo_final.decision_function(X_test)
            y_pred_proba = (decision_scores - decision_scores.min()) / (decision_scores.max() - decision_scores.min())
    except Exception as e:
        print(f"Advertencia: No pude obtener probabilidades - {e}")
    
    # Métricas
    acc = accuracy_score(y_test, y_pred)
    prec = precision_score(y_test, y_pred)
    rec = recall_score(y_test, y_pred)
    f1 = f1_score(y_test, y_pred)
    
    roc_auc = None
    if y_pred_proba is not None:
        roc_auc = roc_auc_score(y_test, y_pred_proba)
    
    print(f"Accuracy: {acc:.4f}")
    print(f"Precision: {prec:.4f}")
    print(f"Recall: {rec:.4f}")
    print(f"F1-Score: {f1:.4f}")
    if roc_auc:
        print(f"ROC-AUC: {roc_auc:.4f}")
    print(f"Tiempo: {train_time:.2f}s")
    
    # Información específica del SVM
    if hasattr(modelo, 'support_'):
        n_support = len(modelo.support_)
        print(f"Support Vectors: {n_support} ({n_support/len(X_train)*100:.1f}%)")
    
    # Validación cruzada (solo con el modelo base, no calibrado para velocidad)
    try:
        cv_f1 = cross_val_score(modelo, X_train, y_train, cv=cv, scoring='f1', n_jobs=1)
        print(f"CV F1: {cv_f1.mean():.4f} (+/- {cv_f1.std() * 2:.4f})")
    except Exception as e:
        print(f"CV falló: {e}")
        cv_f1 = np.array([0])
    
    # Guardar resultados
    resultado = {
        'nombre': nombre,
        'tipo_svm': type(modelo).__name__,
        'parametros': modelo.get_params(),
        'calibrado': usar_calibracion,
        'tiempo_entrenamiento': train_time,
        'n_support_vectors': len(modelo.support_) if hasattr(modelo, 'support_') else None,
        'metricas': {
            'accuracy': acc,
            'precision': prec,
            'recall': rec,
            'f1': f1,
            'roc_auc': roc_auc
        },
        'cv_f1_mean': cv_f1.mean(),
        'cv_f1_std': cv_f1.std()
    }
    
    # Genero visualizaciones
    generar_graficas_svm(nombre, y_test, y_pred, y_pred_proba, resultado)
    
    return resultado

def generar_graficas_svm(nombre, y_true, y_pred, y_pred_proba, resultado):
    """
    Genero visualizaciones específicas para SVM.
    """
    # Matriz de confusión
    cm = confusion_matrix(y_true, y_pred)
    
    # Info adicional en el título
    support_info = ""
    if resultado['n_support_vectors']:
        support_info = f", SVs: {resultado['n_support_vectors']}"
    
    fig_cm = ff.create_annotated_heatmap(
        z=cm,
        x=['Pred: Falso', 'Pred: Verdadero'],
        y=['Real: Falso', 'Real: Verdadero'],
        annotation_text=[[f'{cm[0,0]}', f'{cm[0,1]}'], [f'{cm[1,0]}', f'{cm[1,1]}']],
        colorscale='Oranges'
    )
    
    fig_cm.update_layout(
        title=f'Matriz Confusión - {nombre}<br>F1: {resultado["metricas"]["f1"]:.3f}{support_info}'
    )
    fig_cm.show()
    
    # Solo genero curvas si tengo probabilidades
    if y_pred_proba is not None:
        # ROC y PR curves
        fpr, tpr, _ = roc_curve(y_true, y_pred_proba)
        precision_vals, recall_vals, _ = precision_recall_curve(y_true, y_pred_proba)
        
        fig_curves = make_subplots(
            rows=1, cols=2,
            subplot_titles=[f'ROC (AUC={auc(fpr, tpr):.3f})',
                           f'Precision-Recall (AP={average_precision_score(y_true, y_pred_proba):.3f})']
        )
        
        fig_curves.add_trace(
            go.Scatter(x=fpr, y=tpr, mode='lines', name='ROC'),
            row=1, col=1
        )
        
        fig_curves.add_trace(
            go.Scatter(x=recall_vals, y=precision_vals, mode='lines', name='PR'),
            row=1, col=2
        )
        
        fig_curves.update_layout(
            title=f'Curvas de Evaluación - {nombre}',
            showlegend=False
        )
        fig_curves.show()
        
        # Distribución de scores/probabilidades
        fig_dist = px.histogram(
            x=y_pred_proba,
            color=[f'Clase {int(c)}' for c in y_true],
            title=f'Distribución de Scores - {nombre}<br>Calibrado: {resultado["calibrado"]}',
            opacity=0.7
        )
        fig_dist.show()

print("Funciones de evaluación para SVM listas")

Funciones de evaluación para SVM listas


## LinearSVC - Rápido para datasets grandes

Empiezo con LinearSVC que es más eficiente para datasets grandes.

In [4]:
print("\n=== LINEAR SVM (LinearSVC) ===")

# LinearSVC básico
linear_svm_basic = LinearSVC(
    C=1.0,
    penalty='l2',
    loss='squared_hinge',
    dual=False,  # Dual=False es más eficiente cuando n_samples > n_features
    max_iter=2000,
    random_state=RANDOM_STATE
)

resultados_svm['LinearSVC_Basic'] = evaluar_svm(
    linear_svm_basic, 'LinearSVC Basic (C=1.0)', 
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=True
)

# LinearSVC con regularización baja (C alto)
linear_svm_low_reg = LinearSVC(
    C=10.0,  # Menos regularización
    penalty='l2',
    loss='squared_hinge',
    dual=False,
    max_iter=2000,
    random_state=RANDOM_STATE
)

resultados_svm['LinearSVC_LowReg'] = evaluar_svm(
    linear_svm_low_reg, 'LinearSVC Low Reg (C=10.0)',
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=True
)

# LinearSVC con regularización alta (C bajo)
linear_svm_high_reg = LinearSVC(
    C=0.1,  # Más regularización
    penalty='l2',
    loss='squared_hinge',
    dual=False,
    max_iter=2000,
    random_state=RANDOM_STATE
)

resultados_svm['LinearSVC_HighReg'] = evaluar_svm(
    linear_svm_high_reg, 'LinearSVC High Reg (C=0.1)',
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=True
)

# LinearSVC con L1 penalty
linear_svm_l1 = LinearSVC(
    C=1.0,
    penalty='l1',  # L1 para feature selection
    loss='squared_hinge',
    dual=False,  # dual debe ser False para L1
    max_iter=2000,
    random_state=RANDOM_STATE
)

resultados_svm['LinearSVC_L1'] = evaluar_svm(
    linear_svm_l1, 'LinearSVC L1 Penalty (C=1.0)',
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=True
)


=== LINEAR SVM (LinearSVC) ===

Evaluando: LinearSVC Basic (C=1.0)
--------------------------------------------------
Aplicando calibración para obtener probabilidades...
Accuracy: 0.6389
Precision: 0.6430
Recall: 0.6673
F1-Score: 0.6550
ROC-AUC: 0.6909
Tiempo: 7.84s
CV F1: 0.6508 (+/- 0.0049)



Evaluando: LinearSVC Low Reg (C=10.0)
--------------------------------------------------
Aplicando calibración para obtener probabilidades...
Accuracy: 0.6390
Precision: 0.6431
Recall: 0.6675
F1-Score: 0.6551
ROC-AUC: 0.6909
Tiempo: 8.38s
CV F1: 0.6507 (+/- 0.0050)



Evaluando: LinearSVC High Reg (C=0.1)
--------------------------------------------------
Aplicando calibración para obtener probabilidades...
Accuracy: 0.6389
Precision: 0.6431
Recall: 0.6672
F1-Score: 0.6549
ROC-AUC: 0.6909
Tiempo: 8.20s
CV F1: 0.6509 (+/- 0.0049)



Evaluando: LinearSVC L1 Penalty (C=1.0)
--------------------------------------------------
Aplicando calibración para obtener probabilidades...
Accuracy: 0.6391
Precision: 0.6433
Recall: 0.6675
F1-Score: 0.6552
ROC-AUC: 0.6909
Tiempo: 68.29s
CV F1: 0.6509 (+/- 0.0049)


## SVC con kernels básicos

Ahora pruebo SVC con diferentes kernels pero con configuraciones light.

In [5]:
"""
print("=== SVC CON KERNELS BÁSICOS ===")

# SVC RBF con C alto
svc_rbf_highc = SVC(
    C=10.0,
    kernel='rbf',
    gamma='scale',
    probability=True,
    random_state=RANDOM_STATE
)

resultados_svm['SVC_RBF_HighC'] = evaluar_svm(
    svc_rbf_highc, 'SVC RBF High C (C=10.0)',
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=False
)

# SVC Polynomial grado 2 (light)
svc_poly = SVC(
    C=1.0,
    kernel='poly',
    degree=2,  # Grado bajo para que sea light
    gamma='scale',
    probability=True,
    random_state=RANDOM_STATE
)

resultados_svm['SVC_Poly2'] = evaluar_svm(
    svc_poly, 'SVC Polynomial deg=2 (C=1.0)',
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=False
)

# SVC Linear (equivalente a LinearSVC pero con probabilidades nativas)
svc_linear = SVC(
    C=1.0,
    kernel='linear',
    probability=True,  # Para obtener probabilidades directamente
    random_state=RANDOM_STATE
)

resultados_svm['SVC_Linear'] = evaluar_svm(
    svc_linear, 'SVC Linear (C=1.0)',
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=False
)

"""

'\nprint("=== SVC CON KERNELS BÁSICOS ===")\n\n# SVC RBF con C alto\nsvc_rbf_highc = SVC(\n    C=10.0,\n    kernel=\'rbf\',\n    gamma=\'scale\',\n    probability=True,\n    random_state=RANDOM_STATE\n)\n\nresultados_svm[\'SVC_RBF_HighC\'] = evaluar_svm(\n    svc_rbf_highc, \'SVC RBF High C (C=10.0)\',\n    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=False\n)\n\n# SVC Polynomial grado 2 (light)\nsvc_poly = SVC(\n    C=1.0,\n    kernel=\'poly\',\n    degree=2,  # Grado bajo para que sea light\n    gamma=\'scale\',\n    probability=True,\n    random_state=RANDOM_STATE\n)\n\nresultados_svm[\'SVC_Poly2\'] = evaluar_svm(\n    svc_poly, \'SVC Polynomial deg=2 (C=1.0)\',\n    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=False\n)\n\n# SVC Linear (equivalente a LinearSVC pero con probabilidades nativas)\nsvc_linear = SVC(\n    C=1.0,\n    kernel=\'linear\',\n    probability=True,  # Para obtener probabilidades directamente\n    random_state=RANDO

## Nu-SVM - Diferente enfoque de regularización

Nu-SVM usa un parámetro nu en lugar de C para controlar el número de support vectors.

In [6]:
print("\n=== NU-SVM VARIANTES ===")

"""
# Nu-SVM con nu bajo (menos support vectors)
nu_svm_low = NuSVC(
    nu=0.2,
    kernel='rbf',
    gamma='scale',
    probability=True,
    random_state=RANDOM_STATE
)

resultados_svm['NuSVM_Low'] = evaluar_svm(
    nu_svm_low, 'Nu-SVM Low (nu=0.2)',
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=False
)

# Nu-SVM con kernel linear
nu_svm_linear = NuSVC(
    nu=0.3,
    kernel='linear',
    probability=True,
    random_state=RANDOM_STATE
)

resultados_svm['NuSVM_Linear'] = evaluar_svm(
    nu_svm_linear, 'Nu-SVM Linear (nu=0.3)',
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=False
)
"""


=== NU-SVM VARIANTES ===


"\n# Nu-SVM con nu bajo (menos support vectors)\nnu_svm_low = NuSVC(\n    nu=0.2,\n    kernel='rbf',\n    gamma='scale',\n    probability=True,\n    random_state=RANDOM_STATE\n)\n\nresultados_svm['NuSVM_Low'] = evaluar_svm(\n    nu_svm_low, 'Nu-SVM Low (nu=0.2)',\n    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=False\n)\n\n# Nu-SVM con kernel linear\nnu_svm_linear = NuSVC(\n    nu=0.3,\n    kernel='linear',\n    probability=True,\n    random_state=RANDOM_STATE\n)\n\nresultados_svm['NuSVM_Linear'] = evaluar_svm(\n    nu_svm_linear, 'Nu-SVM Linear (nu=0.3)',\n    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=False\n)\n"

## Configuraciones especiales de SVM

Pruebo algunas configuraciones adicionales con diferentes gammas y parámetros.

In [7]:
print("\n=== CONFIGURACIONES ESPECIALES ===")

"""
# SVC RBF con gamma manual bajo
svc_rbf_lowgamma = SVC(
    C=1.0,
    kernel='rbf',
    gamma=0.001,  # Gamma muy bajo = decisión boundary más suave
    probability=True,
    random_state=RANDOM_STATE
)

resultados_svm['SVC_RBF_LowGamma'] = evaluar_svm(
    svc_rbf_lowgamma, 'SVC RBF Low Gamma (0.001)',
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=False
)

# SVC RBF con gamma alto
svc_rbf_highgamma = SVC(
    C=1.0,
    kernel='rbf',
    gamma=0.1,  # Gamma alto = decisión boundary más compleja
    probability=True,
    random_state=RANDOM_STATE
)

resultados_svm['SVC_RBF_HighGamma'] = evaluar_svm(
    svc_rbf_highgamma, 'SVC RBF High Gamma (0.1)',
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=False
)

# SVC con kernel sigmoid
svc_sigmoid = SVC(
    C=1.0,
    kernel='sigmoid',
    gamma='scale',
    probability=True,
    random_state=RANDOM_STATE
)

resultados_svm['SVC_Sigmoid'] = evaluar_svm(
    svc_sigmoid, 'SVC Sigmoid (C=1.0)',
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=False
) """

# LinearSVC con parámetros balanceados para clases
linear_svm_balanced = LinearSVC(
    C=1.0,
    penalty='l2',
    loss='squared_hinge',
    dual=False,
    class_weight='balanced',  # Ajusta por desbalance de clases
    max_iter=2000,
    random_state=RANDOM_STATE
)

resultados_svm['LinearSVC_Balanced'] = evaluar_svm(
    linear_svm_balanced, 'LinearSVC Balanced (C=1.0)',
    X_train_scaled, X_test_scaled, y_train, y_test, cv, usar_calibracion=True
)


=== CONFIGURACIONES ESPECIALES ===

Evaluando: LinearSVC Balanced (C=1.0)
--------------------------------------------------
Aplicando calibración para obtener probabilidades...
Accuracy: 0.6390
Precision: 0.6432
Recall: 0.6674
F1-Score: 0.6551
ROC-AUC: 0.6909
Tiempo: 13.04s
CV F1: 0.6397 (+/- 0.0060)


## Comparación Final de SVM

Comparo todos los modelos SVM probados.

In [8]:
print("\n" + "="*80)
print("COMPARACIÓN FINAL - MODELOS SVM")
print("="*80)

# Crear tabla comparativa
tabla_svm = []
for nombre, resultado in resultados_svm.items():
    tabla_svm.append({
        'Modelo': nombre,
        'Tipo': resultado['tipo_svm'],
        'F1-Score': resultado['metricas']['f1'],
        'Accuracy': resultado['metricas']['accuracy'],
        'ROC-AUC': resultado['metricas']['roc_auc'] or 0,
        'Tiempo': resultado['tiempo_entrenamiento'],
        'Support_Vectors': resultado['n_support_vectors'] or 0,
        'Calibrado': resultado['calibrado'],
        'CV_F1': resultado['cv_f1_mean']
    })

df_svm = pd.DataFrame(tabla_svm)
df_svm = df_svm.sort_values('F1-Score', ascending=False)

print("\nRanking por F1-Score:")
for i, (_, row) in enumerate(df_svm.iterrows(), 1):
    sv_info = f"SVs: {row['Support_Vectors']:,}" if row['Support_Vectors'] > 0 else "N/A"
    cal_info = "(Cal)" if row['Calibrado'] else ""
    print(f"{i:2d}. {row['Modelo']:<25} F1: {row['F1-Score']:.4f} | "
          f"{row['Tipo']:<10} | {sv_info:<12} | {row['Tiempo']:.1f}s {cal_info}")

# Mejor SVM
mejor_svm = df_svm.iloc[0]
print(f"\n🏆 Mejor SVM: {mejor_svm['Modelo']}")
print(f"   F1-Score: {mejor_svm['F1-Score']:.4f}")
print(f"   Tipo: {mejor_svm['Tipo']}")
print(f"   Tiempo: {mejor_svm['Tiempo']:.2f}s")
if mejor_svm['Support_Vectors'] > 0:
    print(f"   Support Vectors: {mejor_svm['Support_Vectors']:,}")

# Visualizaciones comparativas
fig_svm_comparison = px.bar(
    df_svm.head(10),
    x='F1-Score',
    y='Modelo',
    color='Tipo',
    title='Comparación F1-Score - Top 10 Modelos SVM',
    orientation='h'
)
fig_svm_comparison.update_layout(yaxis={'categoryorder': 'total ascending'})
fig_svm_comparison.show()

# Análisis de Support Vectors vs Performance
df_svm_sv = df_svm[df_svm['Support_Vectors'] > 0]  # Solo los que tienen SVs
if len(df_svm_sv) > 0:
    fig_sv_analysis = px.scatter(
        df_svm_sv,
        x='Support_Vectors',
        y='F1-Score',
        color='Tipo',
        size='Tiempo',
        hover_data=['Modelo'],
        title='Support Vectors vs F1-Score (tamaño = tiempo)'
    )
    fig_sv_analysis.show()

# Tiempo vs Performance
fig_time_perf = px.scatter(
    df_svm,
    x='Tiempo',
    y='F1-Score',
    color='Tipo',
    hover_data=['Modelo'],
    title='Tiempo de Entrenamiento vs F1-Score'
)
fig_time_perf.show()

# Estadísticas por tipo de SVM
print("\nEstadísticas por tipo de SVM:")
stats_by_type = df_svm.groupby('Tipo').agg({
    'F1-Score': ['mean', 'max', 'count'],
    'Tiempo': ['mean', 'min', 'max']
}).round(4)

for tipo in stats_by_type.index:
    print(f"\n{tipo}:")
    print(f"  F1 promedio: {stats_by_type.loc[tipo, ('F1-Score', 'mean')]:.4f}")
    print(f"  F1 máximo: {stats_by_type.loc[tipo, ('F1-Score', 'max')]:.4f}")
    print(f"  Modelos: {int(stats_by_type.loc[tipo, ('F1-Score', 'count')])}")
    print(f"  Tiempo promedio: {stats_by_type.loc[tipo, ('Tiempo', 'mean')]:.2f}s")

# Guardar resultados
os.makedirs('../models', exist_ok=True)
with open('../models/resultados_svm.json', 'w') as f:
    json.dump(resultados_svm, f, indent=2)

df_svm.to_csv('../models/comparacion_svm.csv', index=False)

print(f"\n✓ Resultados guardados en ../models/")
print(f"✓ {len(resultados_svm)} modelos SVM evaluados")
print(f"✓ Mejor F1-Score: {mejor_svm['F1-Score']:.4f}")
print(f"✓ SVM más rápido: {df_svm.loc[df_svm['Tiempo'].idxmin(), 'Modelo']} ({df_svm['Tiempo'].min():.2f}s)")


COMPARACIÓN FINAL - MODELOS SVM

Ranking por F1-Score:
 1. LinearSVC_L1              F1: 0.6552 | LinearSVC  | N/A          | 68.3s (Cal)
 2. LinearSVC_LowReg          F1: 0.6551 | LinearSVC  | N/A          | 8.4s (Cal)
 3. LinearSVC_Balanced        F1: 0.6551 | LinearSVC  | N/A          | 13.0s (Cal)
 4. LinearSVC_Basic           F1: 0.6550 | LinearSVC  | N/A          | 7.8s (Cal)
 5. LinearSVC_HighReg         F1: 0.6549 | LinearSVC  | N/A          | 8.2s (Cal)

🏆 Mejor SVM: LinearSVC_L1
   F1-Score: 0.6552
   Tipo: LinearSVC
   Tiempo: 68.29s



Estadísticas por tipo de SVM:

LinearSVC:
  F1 promedio: 0.6550
  F1 máximo: 0.6552
  Modelos: 5
  Tiempo promedio: 21.15s

✓ Resultados guardados en ../models/
✓ 5 modelos SVM evaluados
✓ Mejor F1-Score: 0.6552
✓ SVM más rápido: LinearSVC_Basic (7.84s)
